In [23]:
from sklearn.model_selection import KFold
import pandas as pd

In [24]:
import wandb
wandb.login()

True

In [25]:
sweep_config = {
    'method': 'random'
}

In [26]:
metric = {
    'name': 'Grand Mean',
    'goal': 'maximize'
}

sweep_config['metric'] = metric

In [27]:
parameters_dict = {
    'dropout': {
          'values': [0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]
        },

    'learning_rate': {
        'distribution': 'uniform',
        'min': 0,
        'max': 0.1
        },

    'batch_size': {
        'values': [256, 512, 1024, 2048, 4096]
        },

    'data_augmentation_multiple': {
        'values': [1, 3, 5, 7]
        }
}

In [28]:
sweep_config['parameters'] = parameters_dict

In [29]:
sweep_id = wandb.sweep(sweep_config, project="pytorch-sweeps-sub_loc_train_only_smote")

Create sweep with ID: pi28mkaa
Sweep URL: https://wandb.ai/imucs/pytorch-sweeps-sub_loc_train_only_smote/sweeps/pi28mkaa


In [30]:
import pprint

pprint.pprint(sweep_config)

{'method': 'random',
 'metric': {'goal': 'maximize', 'name': 'Grand Mean'},
 'parameters': {'batch_size': {'values': [256, 512, 1024, 2048, 4096]},
                'data_augmentation_multiple': {'values': [1, 3, 5, 7]},
                'dropout': {'values': [0.1,
                                       0.2,
                                       0.3,
                                       0.4,
                                       0.5,
                                       0.6,
                                       0.7,
                                       0.8,
                                       0.9]},
                'learning_rate': {'distribution': 'uniform',
                                  'max': 0.1,
                                  'min': 0}}}


In [31]:
feature_pd = pd.read_csv('/home/kongge/projects/new_protT5/data/DPC_T5_578_right.csv')
labels_pd = pd.read_csv("/home/kongge/projects/new_protT5/data/mutil_label_578.csv")

In [32]:
from dataAug.tools import MLDA

In [33]:
from dataAug.all_tools import dataAugSMOTE

In [34]:

smote_multiple = {}

In [35]:
import time
from classify.targeTools import testThresholdFive, Accuracy
from torch import optim
from torch.utils.data import DataLoader, TensorDataset
import torch
from Classify_adjust import ModelClassify
def train_and_val(config=None):
    with wandb.init(config=config):
        config = wandb.config
        kf = KFold(n_splits=10, shuffle=True)
        model_discord = []
        for train_index, test_index in kf.split(feature_pd):
            train_true_data = feature_pd.iloc[train_index]
            train_true_label = labels_pd.iloc[train_index]

            G_feature, G_label = dataAugSMOTE(train_true_data, train_true_label, config.data_augmentation_multiple, 1424)
            train_feature = pd.concat([train_true_data, G_feature], axis=0)
            train_label = pd.concat([train_true_label, G_label], axis=0)

            test_data = feature_pd.iloc[test_index]
            test_label = labels_pd.iloc[test_index]

            datasetTrain = TensorDataset(torch.tensor(train_feature.values), torch.tensor(train_label.values))
            batch_size = config.batch_size
            dataloaderTrain = DataLoader(datasetTrain, batch_size=batch_size, shuffle=True)

            datasetTest = TensorDataset(torch.tensor(test_data.values), torch.tensor(test_label.values))

            batch_size = len(datasetTest)
            dataloaderTest = DataLoader(datasetTest, batch_size=batch_size, shuffle=False)

            model = ModelClassify(drop_rate=config.dropout, num_class=5, feature_num=1424)
            criterion = torch.nn.BCELoss()
            optimizer = optim.Adam(model.parameters(), lr=config.learning_rate)
            import warnings
            warnings.filterwarnings("ignore")
            GMList = {}
            epochs = 200
            for epoch in range(epochs):
                model.train()
                total_loss = 0.0
                for idx, data in enumerate(dataloaderTrain, 0):
                    inputs, labels = data
                    labels = labels.float()
                    inputs = inputs.float()
                    out = model(inputs)
                    loss = criterion(out, labels)
                    optimizer.zero_grad()
                    loss.backward()
                    optimizer.step()
                    total_loss += loss.item()
                avg_loss = total_loss / len(dataloaderTrain)
                threshold = 0.5
                labels_cov = torch.where(out > threshold, torch.tensor(1), torch.tensor(0))
                print(f"Epoch [{epoch+1}/{epochs}], Average Loss: {avg_loss:.4f}, ACC: {Accuracy(labels.int(), labels_cov)}")
                GMScore1 = testThresholdFive(epoch, model, dataloaderTest, class_num=5)
                GMList[epoch] = GMScore1
            t = time.time()
            best_key = max(GMList, key=GMList.get)
            best_value = GMList[best_key]
            best_value = [x.item() if isinstance(x, torch.Tensor) else x for x in best_value]
            model_discord.append(best_value)
        model_discord_column_means = [sum(col) / len(col) for col in zip(*model_discord)]
        smote_multiple[int(t)] = model_discord_column_means
        wandb.log({"Grand Mean": model_discord_column_means[0]})

In [36]:
wandb.agent(sweep_id, train_and_val, count=20)

wandb: Agent Starting Run: 24m4jj5b with config:
wandb: 	batch_size: 2048
wandb: 	data_augmentation_multiple: 3
wandb: 	dropout: 0.8
wandb: 	learning_rate: 0.013940153742164264


Epoch [1/200], Average Loss: 0.7073, ACC: 0.1845614035087719
epoch:0, bestThreshold:[0.13, 0.83, 0.25, 0.34, 0.62], GM:0.42862066626548767, OAA:0.034482758620689655, ACC:0.38505747126436785, F1:0.51666659116745
Epoch [2/200], Average Loss: 0.6659, ACC: 0.3385964912280702
epoch:1, bestThreshold:[0.01, 0.97, 0.24, 0.23, 0.01], GM:0.39465516805648804, OAA:0.034482758620689655, ACC:0.34482758620689646, F1:0.46896544098854065
Epoch [3/200], Average Loss: 0.6051, ACC: 0.3535087719298245
epoch:2, bestThreshold:[0.5, 0.98, 0.97, 0.05, 0.97], GM:0.5247126817703247, OAA:0.3448275862068966, ACC:0.5057471264367815, F1:0.5660918951034546
Epoch [4/200], Average Loss: 0.5103, ACC: 0.4263157894736842
epoch:3, bestThreshold:[0.01, 0.86, 0.45, 0.98, 0.34], GM:0.46264368295669556, OAA:0.25862068965517243, ACC:0.43534482758620685, F1:0.5057470202445984
Epoch [5/200], Average Loss: 0.4494, ACC: 0.4350877192982456
epoch:4, bestThreshold:[0.01, 0.97, 0.45, 0.43, 0.97], GM:0.5527585744857788, OAA:0.4310344827

wandb: Agent Starting Run: t28bqm4v with config:
wandb: 	batch_size: 2048
wandb: 	data_augmentation_multiple: 7
wandb: 	dropout: 0.2
wandb: 	learning_rate: 0.06482808769484193


Epoch [1/200], Average Loss: 0.9540, ACC: 0.2867298578199054
epoch:0, bestThreshold:[0.01, 0.01, 0.44, 0.03, 0.01], GM:0.28091952204704285, OAA:0.0, ACC:0.20833333333333331, F1:0.3155171573162079
Epoch [2/200], Average Loss: 0.4553, ACC: 0.5213270142180095
epoch:1, bestThreshold:[0.01, 0.84, 0.02, 0.01, 0.55], GM:0.4505172371864319, OAA:0.27586206896551724, ACC:0.4224137931034483, F1:0.4839079678058624
Epoch [3/200], Average Loss: 0.2653, ACC: 0.6611374407582938
epoch:2, bestThreshold:[0.01, 0.29, 0.01, 0.81, 0.98], GM:0.5126436948776245, OAA:0.39655172413793105, ACC:0.5028735632183907, F1:0.5402297973632812
Epoch [4/200], Average Loss: 0.2375, ACC: 0.7630331753554502
epoch:3, bestThreshold:[0.16, 0.94, 0.98, 0.79, 0.01], GM:0.559195339679718, OAA:0.5517241379310345, ACC:0.5574712643678161, F1:0.5603448152542114
Epoch [5/200], Average Loss: 0.2312, ACC: 0.6824644549763034
epoch:4, bestThreshold:[0.02, 0.9, 0.25, 0.98, 0.01], GM:0.6356321573257446, OAA:0.5689655172413793, ACC:0.62643678

wandb: Sweep Agent: Waiting for job.
wandb: Job received.
wandb: Agent Starting Run: p5m6pv5w with config:
wandb: 	batch_size: 2048
wandb: 	data_augmentation_multiple: 1
wandb: 	dropout: 0.9
wandb: 	learning_rate: 0.01386928187565113


...

Epoch [1/200], Average Loss: 0.7355, ACC: 0.19216651046547853
epoch:0, bestThreshold:[0.25, 0.12, 0.42, 0.06, 0.01], GM:0.327873557806015, OAA:0.034482758620689655, ACC:0.29741379310344834, F1:0.3965516984462738
Epoch [2/200], Average Loss: 0.7255, ACC: 0.20449859418931485
epoch:1, bestThreshold:[0.75, 0.98, 0.98, 0.05, 0.01], GM:0.32862067222595215, OAA:0.05172413793103448, ACC:0.2816091954022989, F1:0.37873557209968567
Epoch [3/200], Average Loss: 0.6699, ACC: 0.2063261480787248
epoch:2, bestThreshold:[0.74, 0.27, 0.18, 0.29, 0.98], GM:0.43390804529190063, OAA:0.29310344827586204, ACC:0.41954022988505746, F1:0.4683907926082611
Epoch [4/200], Average Loss: 0.5239, ACC: 0.4042799125273357
epoch:3, bestThreshold:[0.74, 0.61, 0.97, 0.01, 0.96], GM:0.4585632383823395, OAA:0.3448275862068966, ACC:0.44683908045977005, F1:0.48678162693977356
Epoch [5/200], Average Loss: 0.4188, ACC: 0.45278819119025326
epoch:4, bestThreshold:[0.02, 0.2, 0.98, 0.01, 0.78], GM:0.45160919427871704, OAA:0.362068

wandb: Sweep Agent: Waiting for job.
wandb: Job received.
wandb: Agent Starting Run: 2810hq14 with config:
wandb: 	batch_size: 4096
wandb: 	data_augmentation_multiple: 7
wandb: 	dropout: 0.5
wandb: 	learning_rate: 0.05035680417475822


Epoch [1/200], Average Loss: 0.7720, ACC: 0.1794628751974724
epoch:0, bestThreshold:[0.96, 0.33, 0.96, 0.01, 0.08], GM:0.3408045768737793, OAA:0.0, ACC:0.2887931034482759, F1:0.4080459475517273
Epoch [2/200], Average Loss: 0.7832, ACC: 0.23736176935229072
epoch:1, bestThreshold:[0.01, 0.97, 0.16, 0.44, 0.05], GM:0.41528740525245667, OAA:0.2413793103448276, ACC:0.39080459770114934, F1:0.44999998807907104
Epoch [3/200], Average Loss: 0.3865, ACC: 0.45023696682464454
epoch:2, bestThreshold:[0.33, 0.92, 0.02, 0.29, 0.88], GM:0.3432183861732483, OAA:0.2413793103448276, ACC:0.3261494252873563, F1:0.36264365911483765
Epoch [4/200], Average Loss: 0.3459, ACC: 0.43364928909952605
epoch:3, bestThreshold:[0.37, 0.97, 0.01, 0.98, 0.02], GM:0.43229883909225464, OAA:0.29310344827586204, ACC:0.4094827586206896, F1:0.46034476161003113
Epoch [5/200], Average Loss: 0.3410, ACC: 0.4786729857819905
epoch:4, bestThreshold:[0.97, 0.98, 0.32, 0.97, 0.29], GM:0.4321839213371277, OAA:0.3448275862068966, ACC:0.

wandb: Agent Starting Run: doivlyy9 with config:
wandb: 	batch_size: 4096
wandb: 	data_augmentation_multiple: 5
wandb: 	dropout: 0.4
wandb: 	learning_rate: 0.09149115495446336


Epoch [1/200], Average Loss: 0.7405, ACC: 0.196484942886812
epoch:0, bestThreshold:[0.01, 0.01, 0.79, 0.01, 0.01], GM:0.3757471442222595, OAA:0.10344827586206896, ACC:0.3362068965517241, F1:0.43333327770233154
Epoch [2/200], Average Loss: 1.1644, ACC: 0.18430944963655216
epoch:1, bestThreshold:[0.01, 0.01, 0.01, 0.01, 0.01], GM:0.25839078426361084, OAA:0.0, ACC:0.19971264367816097, F1:0.3005746901035309
Epoch [3/200], Average Loss: 1.5729, ACC: 0.21770508826583665
epoch:2, bestThreshold:[0.01, 0.01, 0.01, 0.01, 0.01], GM:0.41781607270240784, OAA:0.06896551724137931, ACC:0.39080459770114945, F1:0.502873420715332
Epoch [4/200], Average Loss: 0.6562, ACC: 0.3375649013499482
epoch:3, bestThreshold:[0.01, 0.01, 0.01, 0.01, 0.97], GM:0.4833332896232605, OAA:0.3275862068965517, ACC:0.4683908045977011, F1:0.5201148390769958
Epoch [5/200], Average Loss: 0.4118, ACC: 0.4058151609553478
epoch:4, bestThreshold:[0.91, 0.01, 0.87, 0.01, 0.01], GM:0.510919451713562, OAA:0.43103448275862066, ACC:0.505

In [37]:
smote_multiple

{1695115013: [0.868426913022995,
  0.8271324863883848,
  0.8659860859044162,
  0.8760586857795716,
  0.8941923797130584,
  0.8787649095058441],
 1695118605: [0.8954839587211609,
  0.873653962492438,
  0.8941016333938295,
  0.9073653936386108,
  0.9012855410575866,
  0.901013308763504],
 1695121606: [0.7674086451530456,
  0.6817301875378099,
  0.7583257713248639,
  0.7694242835044861,
  0.8407541871070862,
  0.7868088603019714],
 1695125102: [0.9014761030673981,
  0.8822444041137327,
  0.9001461988304094,
  0.9160465836524964,
  0.9027324020862579,
  0.9062109351158142],
 1695128408: [0.8847529828548432,
  0.8599516031457956,
  0.8830207703165959,
  0.8962946236133575,
  0.893400889635086,
  0.8910970032215119],
 1695132182: [0.9010071754455566,
  0.8753781004234724,
  0.8994933454325471,
  0.9129461586475373,
  0.909724748134613,
  0.9074934542179107],
 1695137335: [0.8916108250617981,
  0.8650635208711435,
  0.8898366606170601,
  0.9022232353687286,
  0.9027979373931885,
  0.898132687

In [38]:
import json
file = open("/home/kongge/projects/new_protT5/data/dictionary_data_only_smote.json", "w")
json.dump(smote_multiple, file)
file.close()